# Helpfull

In [1]:
import numpy as np
import plotly.graph_objects as go

class DisplayFigs:
    def _rgb_to_hex(rgb):
        '''Convert colors to Plotly hex color strings'''
        rgb255 = (rgb * 255).astype(int)
        return ['rgb({},{},{})'.format(r, g, b) for r, g, b in rgb255]


    def display_plotly_orig_and_clouds(orig_fig, cloud_figs: set):
        # Extract metadata for origin figure
        verts_fig = np.asarray(orig_fig.vertices)
        tris_fig = np.asarray(orig_fig.triangles)
        orig_colors = np.asarray(orig_fig.vertex_colors) if orig_fig.has_vertex_colors() else np.full(verts_fig.shape, [128/255, 26/255, 107/255])

        # Exrtact metadata for cloud figures
        cloud_figs_points = []
        cloud_figs_colors_hex = []
        for cloud_fig in cloud_figs:
            cloud_figs_points.append(np.asarray(cloud_fig.points))

            fig_colors = np.asarray(cloud_fig.colors) if cloud_fig.has_colors() else np.tile([0, 0, 1], (len(cloud_fig), 1))
            cloud_figs_colors_hex.append(DisplayFigs._rgb_to_hex(fig_colors))

        orig_trace = go.Mesh3d(
            x=verts_fig[:, 0], y=verts_fig[:, 1], z=verts_fig[:, 2],
            i=tris_fig[:, 0], j=tris_fig[:, 1], k=tris_fig[:, 2],
            vertexcolor=orig_colors,
            opacity=0.8,
            showlegend=False,
            name=''
        )

        cloud_figs_trace = []
        for points, colors in zip(cloud_figs_points, cloud_figs_colors_hex):
            cloud_figs_trace.append(go.Scatter3d(
                x=points[:, 0], y=points[:, 1], z=points[:, 2],
                mode='markers',
                marker=dict(size=2, color=colors),
                showlegend=False,
                name=''
            ))

        merged_trace = [orig_trace,] + cloud_figs_trace

        fig = go.Figure(data=merged_trace)

        fig.update_layout(
            showlegend=False,
            scene=dict(
                xaxis=dict(visible=False),
                yaxis=dict(visible=False),
                zaxis=dict(visible=False),
                aspectmode='data'
            ),
            margin=dict(t=0, l=0, r=0, b=0)
        )

        fig.show(config={'displayModeBar': False})


    def display_plotly_origs(orig_figs: set):
        traces = []
        for orig_fig in orig_figs:
            vertices = np.asarray(orig_fig.vertices)
            triangles = np.asarray(orig_fig.triangles)
            color = np.asarray(orig_fig.vertex_colors) if orig_fig.has_vertex_colors() else np.full(vertices.shape, [128/255, 26/255, 107/255])

            traces.append(
                go.Mesh3d(
                    x=vertices[:, 0], y=vertices[:, 1], z=vertices[:, 2],
                    i=triangles[:, 0], j=triangles[:, 1], k=triangles[:, 2],
                    vertexcolor=color,
                    opacity=0.8,
                    showlegend=False,
                    name=''
                )
            )

        fig = go.Figure(data=traces)

        fig.update_layout(
            showlegend=False,
            scene=dict(
                xaxis=dict(visible=False),
                yaxis=dict(visible=False),
                zaxis=dict(visible=False),
                aspectmode='data'
            ),
            margin=dict(t=0, l=0, r=0, b=0)
        )

        fig.show(config={'displayModeBar': False})


    def display_plotly_clouds(cloud_figs: set):
        cloud_figs_trace = []
        for cloud_fig in cloud_figs:
            points = np.asarray(cloud_fig.points)
            color = DisplayFigs._rgb_to_hex(
                np.asarray(cloud_fig.colors) if cloud_fig.has_colors() else np.tile([0, 0, 1], (len(cloud_fig), 1))
            )

            cloud_figs_trace.append(go.Scatter3d(
                x=points[:, 0], y=points[:, 1], z=points[:, 2],
                mode='markers',
                marker=dict(size=2, color=color),
                showlegend=False,
                name=''
            ))

        fig = go.Figure(data=cloud_figs_trace)

        fig.update_layout(
            showlegend=False,
            scene=dict(
                xaxis=dict(visible=False),
                yaxis=dict(visible=False),
                zaxis=dict(visible=False),
                aspectmode='data'
            ),
            margin=dict(t=0, l=0, r=0, b=0)
        )

        fig.show()#config={'displayModeBar': False})

In [2]:
!pip uninstall torch torchao -y
!pip uninstall torchaudio torchdata -y
!pip uninstall torchinfo torchmetrics -y
!pip uninstall torchsummary torchtune torchvision -y
!pip install torch==2.2.2+cu121 torchvision==0.17.2+cu121 --index-url https://download.pytorch.org/whl/cu121
!pip install open3d 
# ! pip install open3d-ml
# !pip install "numpy<2"
# !pip install tensorboard

# http://www.poss.pku.edu.cn./semanticposs.html

Found existing installation: torch 2.6.0+cu124
Uninstalling torch-2.6.0+cu124:
  Successfully uninstalled torch-2.6.0+cu124
Found existing installation: torchao 0.10.0
Uninstalling torchao-0.10.0:
  Successfully uninstalled torchao-0.10.0
Found existing installation: torchaudio 2.6.0+cu124
Uninstalling torchaudio-2.6.0+cu124:
  Successfully uninstalled torchaudio-2.6.0+cu124
Found existing installation: torchdata 0.11.0
Uninstalling torchdata-0.11.0:
  Successfully uninstalled torchdata-0.11.0
Found existing installation: torchinfo 1.8.0
Uninstalling torchinfo-1.8.0:
  Successfully uninstalled torchinfo-1.8.0
Found existing installation: torchmetrics 1.8.2
Uninstalling torchmetrics-1.8.2:
  Successfully uninstalled torchmetrics-1.8.2
Found existing installation: torchsummary 1.5.1
Uninstalling torchsummary-1.5.1:
  Successfully uninstalled torchsummary-1.5.1
Found existing installation: torchtune 0.6.1
Uninstalling torchtune-0.6.1:
  Successfully uninstalled torchtune-0.6.1
Found exist

In [4]:
import warnings
warnings.filterwarnings(
    "ignore",
    message=r"An output with one or more elements was resized",
    category=UserWarning
)

In [5]:
import torch
import numpy as np
import open3d as o3d
import open3d.ml.torch as ml3d
import open3d.ml as o3dml

Jupyter environment detected. Enabling Open3D WebVisualizer.
[Open3D INFO] WebRTC GUI backend enabled.
[Open3D INFO] WebRTCWindowSystem: HTTP handshake server disabled.


2025-11-06 16:44:33.090230: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1762447473.280666      47 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1762447473.327186      47 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


In [6]:
print(torch.__version__)
print(torch.cuda.is_available())
print(np.__version__)
print(o3d.__version__)

2.2.2+cu121
True
1.26.4
0.19.0


In [9]:
import os
import open3d.ml.torch as ml3d

ds = ml3d.datasets.SemanticKITTI(
    dataset_path="/kaggle/input/semanticposs-dataset",
    name="poss",
    cache_dir="./logs/cache_poss_fresh",
    use_cache=False,
    all_split=["00","01","02","03", "04", "05"],
    training_split = ["00","01","02","03"],
    validation_split   = ["05"],
    test_split  = ["04"],
    class_weights=[],
    ignored_label_inds=[],
)

model = ml3d.models.RandLANet(num_classes=ds.num_classes, in_channels=4)

names = ds.get_label_to_names()
num_classes = int(max(names.keys())) + 1
rng = np.random.default_rng(0)
palette = rng.random((num_classes, 3))

In [8]:
names

{0: 'unlabeled',
 1: 'car',
 2: 'bicycle',
 3: 'motorcycle',
 4: 'truck',
 5: 'other-vehicle',
 6: 'person',
 7: 'bicyclist',
 8: 'motorcyclist',
 9: 'road',
 10: 'parking',
 11: 'sidewalk',
 12: 'other-ground',
 13: 'building',
 14: 'fence',
 15: 'vegetation',
 16: 'trunk',
 17: 'terrain',
 18: 'pole',
 19: 'traffic-sign'}

In [ ]:
pipeline = ml3d.pipelines.SemanticSegmentation(
    model=model,
    dataset=ds,
    max_epoch=10,
    batch_size=4,
    val_batch_size=4,
    logs_dir='./poss_logs',
    test_result_folder='./poss_test',
    optimizer={"lr": 0.001},
    device="cuda"
)

# pipeline.load_ckpt(ckpt_path='logs/RandLANet_poss_torch/checkpoint/ckpt_00010.pth', is_resume=False)

In [41]:
dict(pipeline.model.cfg)

{'name': 'RandLANet',
 'num_neighbors': 16,
 'num_layers': 4,
 'num_points': 45056,
 'num_classes': 20,
 'ignored_label_inds': [0],
 'sub_sampling_ratio': [4, 4, 4, 4],
 'in_channels': 4,
 'dim_features': 8,
 'dim_output': [16, 64, 128, 256],
 'grid_size': 0.06,
 'batcher': 'DefaultBatcher',
 'ckpt_path': None,
 'augment': {}}

In [42]:
dict(pipeline.cfg)

{'name': 'SemanticSegmentation',
 'batch_size': 4,
 'val_batch_size': 4,
 'test_batch_size': 3,
 'max_epoch': 10,
 'learning_rate': 0.01,
 'lr_decays': 0.95,
 'save_ckpt_freq': 20,
 'adam_lr': 0.01,
 'scheduler_gamma': 0.95,
 'momentum': 0.98,
 'main_log_dir': './logs/',
 'split': 'train',
 'train_sum_dir': 'train_log',
 'logs_dir': './poss_logs',
 'test_result_folder': './poss_test',
 'optimizer': {'lr': 0.001},
 'summary': {}}

In [ ]:
split = ds.get_split("test")
sample = split.get_data(0)
points = sample["point"].astype(np.float32)
feats = sample["feat"].astype(np.float32)
label = sample["label"].astype(np.int32)

data_infer = {
    "point": points, # координаты точек
    "feat": feats, # координаты точек
    "label": label, # лейблы
    }
res = pipeline.run_inference(data_infer)
pred = np.asarray(res["predict_labels"]).astype(np.int32)

In [51]:
pcd = o3d.geometry.PointCloud(o3d.utility.Vector3dVector(points))
pcd.colors = o3d.utility.Vector3dVector(palette[pred])
# o3d.visualization.draw_geometries([pcd], window_name="RandLA-Net predictions")

DisplayFigs.display_plotly_clouds((pcd,))

In [52]:
pipeline.run_test()


test 0/1: 100%|██████████| 61881/61881 [11:16<00:00, 91.41it/s]   

test 1/500: 100%|██████████| 61668/61668 [00:04<00:00, 14290.42it/s]

test 3/500: 100%|██████████| 61455/61455 [00:04<00:00, 14237.96it/s]

test 5/500: 100%|██████████| 61378/61378 [00:05<00:00, 10549.70it/s]

test 7/500: 100%|██████████| 61531/61531 [00:05<00:00, 11003.61it/s]

test 9/500: 100%|██████████| 61371/61371 [00:04<00:00, 13861.15it/s]

test 11/500: 100%|██████████| 61153/61153 [00:05<00:00, 10403.30it/s]

test 13/500: 100%|██████████| 60857/60857 [00:04<00:00, 13753.28it/s]

test 15/500: 100%|██████████| 60735/60735 [00:04<00:00, 14074.09it/s]

test 17/500: 100%|██████████| 60550/60550 [00:05<00:00, 10318.56it/s]

test 19/500: 100%|██████████| 60601/60601 [00:05<00:00, 10759.10it/s]

test 21/500: 100%|██████████| 61023/61023 [00:04<00:00, 13800.40it/s]

test 23/500: 100%|██████████| 61023/61023 [00:04<00:00, 14144.13it/s]

test 25/500: 100%|██████████| 61481/61481 [00:04<00:00, 14097.18it/s]

test 27/500: 

In [54]:
# Сохранение модели
import torch

torch.save(pipeline.model.state_dict(), "semantic_segmentation_model.pth")


# Train

In [9]:
!ls /kaggle/input/semantic-segmentation-model/pytorch/default/1

semantic_segmentation_model.pth


In [10]:
# Загрузка весов модели
model_check = ml3d.models.RandLANet(num_classes=ds.num_classes, in_channels=4)
model_check.load_state_dict(torch.load("/kaggle/input/semantic-segmentation-model/pytorch/default/1/semantic_segmentation_model.pth"))

<All keys matched successfully>

In [11]:
train_split = ds.get_split("training")
print(train_split.get_data(0)['point'].shape)

val_split = ds.get_split("validation")
print(val_split.get_data(0)['point'].shape)

test_split = ds.get_split("test")
print(test_split.get_data(0)['point'].shape)

(66658, 3)
(66534, 3)
(66303, 3)


In [12]:
test_split.get_data(0).keys()

dict_keys(['point', 'feat', 'label'])

In [13]:
pipeline = ml3d.pipelines.SemanticSegmentation(
    model=model_check,
    dataset=ds,
    max_epoch=10,
    batch_size=4,
    val_batch_size=4,
    logs_dir='./poss_logs',
    test_result_folder='./poss_test',
    optimizer={"lr": 0.001},
    device="cuda"
)

In [14]:
pipeline.run_train()

training:   0%|          | 0/497 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/open3d/_ml3d/torch/dataloaders/default_batcher.py:48: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  storage = elem.storage()._new_shared(numel)
/usr/local/lib/python3.11/dist-packages/open3d/_ml3d/torch/dataloaders/default_batcher.py:48: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  storage = elem.storage()._new_shared(numel)
validation:   0%|          | 0/125 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/open3d/_ml

In [15]:
pipeline.run_test()

test 0/500: 100%|██████████| 61881/61881 [00:04<00:00, 13040.98it/s]

test 2/500: 100%|██████████| 61514/61514 [00:04<00:00, 13012.49it/s]

test 4/500: 100%|██████████| 61472/61472 [00:04<00:00, 12870.51it/s]

test 6/500: 100%|██████████| 61421/61421 [00:04<00:00, 12907.82it/s]

test 8/500: 100%|██████████| 61589/61589 [00:04<00:00, 13087.08it/s]

test 10/500: 100%|██████████| 61241/61241 [00:06<00:00, 9795.96it/s] 

test 12/500: 100%|██████████| 60867/60867 [00:04<00:00, 12930.45it/s]

test 14/500: 100%|██████████| 60672/60672 [00:04<00:00, 12653.68it/s]

test 16/500: 100%|██████████| 60630/60630 [00:04<00:00, 12838.20it/s]

test 18/500: 100%|██████████| 60642/60642 [00:04<00:00, 12900.43it/s]

test 20/500: 100%|██████████| 60827/60827 [00:04<00:00, 12894.20it/s]

test 22/500: 100%|██████████| 61031/61031 [00:06<00:00, 9851.66it/s] 

test 24/500: 100%|██████████| 61246/61246 [00:04<00:00, 12978.23it/s]

test 26/500: 100%|██████████| 61490/61490 [00:06<00:00, 9764.90it/s] 

test 28/500

# **Домашнее задание №1: Построение сложной сцены из облаков точек**


1. **Настройка среды**

Настройте среду для запуска модели

2. **Запуск**

    * Инициализируйте пустые веса модели
    * Попробуйте модель на одном из примеров
    * Инициализируйте предобученную модель из файла `randlanet_semantickitti_202201071330utc.pth`
    * Попробуйте модель на одном из примеров

3. **Обучение**

   * Обучите модель на датасете [POSS](http://www.poss.pku.edu.cn./semanticposs.html)

4. **Тестирование**

   * Выполните тест модели и посчитайте метрики

5. **Критерии успешности выполнения задания**

   * настроенная среда
   * обученная модель
   * метрика `Overall Testing Accuracy` > 0.55

In [29]:
def overall_accuracy(predicted, labels):
    correct = (predicted == labels).sum()
    print(f'corrected count: {correct} from {len(predicted)}')
    total = labels.size
    accuracy = correct / total
    return accuracy

In [30]:
ds = ml3d.datasets.SemanticKITTI(
    dataset_path="/kaggle/input/semanticposs-dataset",
    name="poss",
    cache_dir="./logs/cache_poss_fresh",
    use_cache=False,
    all_split=["00","01","02","03", "04", "05"],
    training_split = ["00","01","02","03"],
    validation_split   = ["05"],
    test_split  = ["04"],
    class_weights=[],
    ignored_label_inds=[],
)

model = ml3d.models.RandLANet(num_classes=ds.num_classes, in_channels=4)

names = ds.get_label_to_names()
num_classes = int(max(names.keys())) + 1
rng = np.random.default_rng(0)
palette = rng.random((num_classes, 3))

#### Get predict to empty weight model

In [31]:
model = ml3d.models.RandLANet(num_classes=ds.num_classes, in_channels=4)

In [32]:
pipeline = ml3d.pipelines.SemanticSegmentation(
    model=model,
    dataset=ds,
    max_epoch=10,
    batch_size=4,
    val_batch_size=4,
    logs_dir='./poss_logs',
    test_result_folder='./poss_test',
    optimizer={"lr": 0.001},
    device="cuda"
)

In [33]:
split = ds.get_split("test")
sample = split.get_data(0)
points = sample["point"].astype(np.float32)
feats = sample["feat"].astype(np.float32)
label = sample["label"].astype(np.int32)

data_infer = {
    "point": points, # координаты точек
    "feat": feats, # координаты точек
    "label": label, # лейблы
    }
res = pipeline.run_inference(data_infer)
pred = np.asarray(res["predict_labels"]).astype(np.int32)

test 0/1: 100%|██████████| 61881/61881 [00:00<00:00, 66996.19it/s]

In [34]:
overall_accuracy(pred, label)

corrected count: 40 from 66303


0.0006032909521439452

test 0/1: 100%|██████████| 61881/61881 [00:16<00:00, 66996.19it/s]

#### Get predict from pretrain model

In [13]:
model = ml3d.models.RandLANet()

checkpoint = torch.load('/kaggle/input/randlanet-semantickitti-202201071330utc/pytorch/default/1/randlanet_semantickitti_202201071330utc.pth')
pretrained_dict = checkpoint['model_state_dict']
model.load_state_dict(pretrained_dict)

<All keys matched successfully>

In [14]:
pipeline = ml3d.pipelines.SemanticSegmentation(
    model=model,
    dataset=ds,
    max_epoch=10,
    batch_size=4,
    val_batch_size=4,
    logs_dir='./poss_logs',
    test_result_folder='./poss_test',
    optimizer={"lr": 0.001},
    device="cuda"
)

test 0/1: 100%|██████████| 61881/61881 [00:01<00:00, 39029.84it/s]


In [25]:
split = ds.get_split("test")
sample = split.get_data(0)
points = sample["point"].astype(np.float32)
feats = sample["feat"].astype(np.float32)
label = sample["label"].astype(np.int32)

data_infer = {
    "point": points, # координаты точек
    # "feat": feats, # координаты точек
    "label": label, # лейблы
    }
res = pipeline.run_inference(data_infer)
pred = np.asarray(res["predict_labels"]).astype(np.int32)

test 0/1: 100%|██████████| 61881/61881 [00:01<00:00, 52411.87it/s]

#### Train model

In [15]:
model = ml3d.models.RandLANet(num_classes=ds.num_classes, in_channels=4)

In [16]:
pipeline = ml3d.pipelines.SemanticSegmentation(
    model=model,
    dataset=ds,
    max_epoch=10,
    batch_size=4,
    val_batch_size=4,
    logs_dir='./poss_logs',
    test_result_folder='./poss_test',
    optimizer={"lr": 0.001},
    device="cuda"
)

In [17]:
pipeline.run_train()

training:   0%|          | 0/497 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/open3d/_ml3d/torch/dataloaders/default_batcher.py:48: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  storage = elem.storage()._new_shared(numel)
/usr/local/lib/python3.11/dist-packages/open3d/_ml3d/torch/dataloaders/default_batcher.py:48: UserWarning: TypedStorage is deprecated. It will be removed in the future and UntypedStorage will be the only storage class. This should only matter to you if you are using storages directly.  To access UntypedStorage directly, use tensor.untyped_storage() instead of tensor.storage()
  storage = elem.storage()._new_shared(numel)
validation:   0%|          | 0/125 [00:00<?, ?it/s]/usr/local/lib/python3.11/dist-packages/open3d/_ml

In [19]:
res = pipeline.run_test()

test 0/500: 100%|██████████| 61881/61881 [00:04<00:00, 12882.10it/s]

test 2/500: 100%|██████████| 61514/61514 [00:04<00:00, 12801.81it/s]

test 4/500: 100%|██████████| 61472/61472 [00:04<00:00, 12816.03it/s]

test 6/500: 100%|██████████| 61421/61421 [00:04<00:00, 12858.49it/s]

test 8/500: 100%|██████████| 61589/61589 [00:04<00:00, 12955.05it/s]

test 10/500: 100%|██████████| 61241/61241 [00:06<00:00, 9791.88it/s] 

test 12/500: 100%|██████████| 60867/60867 [00:04<00:00, 12819.79it/s]

test 14/500: 100%|██████████| 60672/60672 [00:04<00:00, 12828.95it/s]

test 16/500: 100%|██████████| 60630/60630 [00:04<00:00, 12712.86it/s]

test 18/500: 100%|██████████| 60642/60642 [00:06<00:00, 9806.09it/s] 

test 20/500: 100%|██████████| 60827/60827 [00:06<00:00, 9783.89it/s] 

test 22/500: 100%|██████████| 61031/61031 [00:06<00:00, 9663.56it/s] 

test 24/500: 100%|██████████| 61246/61246 [00:04<00:00, 13106.22it/s]

test 26/500: 100%|██████████| 61490/61490 [00:04<00:00, 13004.63it/s]

test 28/500

**FINAL TEST SCORES**
- Overall Testing Accuracy : 0.547825427685035
- mIoU : 0.47067603788326984

In [28]:
!cat /kaggle/working/logs/RandLANet_poss_torch/log_test_2025-11-06_18-32-24.txt

ckpt_path not given. Restore from the latest ckpt
Loading checkpoint ./logs/RandLANet_poss_torch/checkpoint/ckpt_00010.pth
Loading checkpoint optimizer_state_dict
Loading checkpoint scheduler_state_dict
Started testing
Accuracy : [0.22087658592848905, 0.271875, 0.9998505343397355, 0.0, 0.7052932761087267, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, 0.43957907927539025]
IoU : [0.21761363636363637, 0.05206463195691203, 0.9816567613177782, 0.0, 0.524468085106383, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, 0.3551606229489419]
Accuracy : [0.2243367935409458, 0.2346456692913386, 0.9999261202024307, 0.0, 0.7057553956834532, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, 0.43293279574363364]
IoU : [0.22014714204867006, 0.04482551143200963, 0.9831117890607975, 0.0, 0.5215311004784688, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, nan, 0.35392310860398923]
Accuracy : [0.219040247678